# Characterizing the general methylation landscape

In this notebook, I will characterize the general methylation landscape. To characterize CpG methylation, I will use individual samples, as well as a union BEDgraph that concatenates all sample information.

1. Concatenate coverage information
2. Characterize methylation for each CpG dinucleotide in individual samples and union BEDgraph
2. Determine genomic location of highly methylated, moderately methylated, and lowly CpGs

## 0. Set working directory

In [1]:
!pwd

/Users/yaaminivenkataraman/Documents/ceabigr/code


In [7]:
cd ../output/

/Users/yaaminivenkataraman/Documents/ceabigr/output


In [8]:
!mkdir methylation-landscape

In [9]:
cd methylation-landscape/

/Users/yaaminivenkataraman/Documents/ceabigr/output/methylation-landscape


In [10]:
#Install pandas for this notebook
import pandas as pd
print(pd.__version__)

Matplotlib is building the font cache using fc-list. This may take a moment.


0.25.1


## 1. Obtain sample BEDgraphs

In [11]:
#Download 5x bedgraphs
!wget -r \
--no-check-certificate --no-directories --no-parent --reject "index.html*" \
-P . \
-A "*5x.bedgraph" https://gannet.fish.washington.edu/seashell/bu-mox/scrubbed/120321-cvBS/

--2022-02-21 12:57:32--  https://gannet.fish.washington.edu/seashell/bu-mox/scrubbed/120321-cvBS/
Resolving gannet.fish.washington.edu (gannet.fish.washington.edu)... 128.95.149.52
Connecting to gannet.fish.washington.edu (gannet.fish.washington.edu)|128.95.149.52|:443... connected.
  Unable to locally verify the issuer's authority.
HTTP request sent, awaiting response... 200 OK
Length: unspecified [text/html]
Saving to: ‘./index.html.tmp’

index.html.tmp          [ <=>                ]  62.99K  --.-KB/s    in 0.03s   

2022-02-21 12:57:35 (1.87 MB/s) - ‘./index.html.tmp’ saved [64500]

Loading robots.txt; please ignore errors.
--2022-02-21 12:57:35--  https://gannet.fish.washington.edu/robots.txt
Reusing existing connection to gannet.fish.washington.edu:443.
HTTP request sent, awaiting response... 404 Not Found
2022-02-21 12:57:35 ERROR 404: Not Found.

Removing ./index.html.tmp since it should be rejected.

--2022-02-21 12:57:35--  https://gannet.fish.washington.edu/seashell/bu-mox/s

--2022-02-21 13:00:17--  https://gannet.fish.washington.edu/seashell/bu-mox/scrubbed/120321-cvBS/31M_R1_val_1_5x.bedgraph
Reusing existing connection to gannet.fish.washington.edu:443.
HTTP request sent, awaiting response... 200 OK
Length: 359342062 (343M)
Saving to: ‘./31M_R1_val_1_5x.bedgraph’

31M_R1_val_1_5x.bed 100%[===================>] 342.69M  14.7MB/s    in 16s     

2022-02-21 13:00:33 (21.9 MB/s) - ‘./31M_R1_val_1_5x.bedgraph’ saved [359342062/359342062]

--2022-02-21 13:00:34--  https://gannet.fish.washington.edu/seashell/bu-mox/scrubbed/120321-cvBS/35F_R1_val_1_5x.bedgraph
Reusing existing connection to gannet.fish.washington.edu:443.
HTTP request sent, awaiting response... 200 OK
Length: 367994058 (351M)
Saving to: ‘./35F_R1_val_1_5x.bedgraph’

35F_R1_val_1_5x.bed 100%[===================>] 350.95M  32.5MB/s    in 14s     

2022-02-21 13:00:48 (24.7 MB/s) - ‘./35F_R1_val_1_5x.bedgraph’ saved [367994058/367994058]

--2022-02-21 13:00:49--  https://gannet.fish.washington.ed

HTTP request sent, awaiting response... 200 OK
Length: unspecified [text/html]
Saving to: ‘./index.html?C=S;O=D.tmp’

index.html?C=S;O=D.     [ <=>                ]  62.99K  --.-KB/s    in 0.03s   

2022-02-21 13:03:57 (2.03 MB/s) - ‘./index.html?C=S;O=D.tmp’ saved [64500]

Removing ./index.html?C=S;O=D.tmp since it should be rejected.

--2022-02-21 13:03:57--  https://gannet.fish.washington.edu/seashell/bu-mox/scrubbed/120321-cvBS/?C=D;O=D
Reusing existing connection to gannet.fish.washington.edu:443.
HTTP request sent, awaiting response... 200 OK
Length: unspecified [text/html]
Saving to: ‘./index.html?C=D;O=D.tmp’

index.html?C=D;O=D.     [ <=>                ]  62.99K  --.-KB/s    in 0.05s   

2022-02-21 13:04:00 (1.22 MB/s) - ‘./index.html?C=D;O=D.tmp’ saved [64500]

Removing ./index.html?C=D;O=D.tmp since it should be rejected.

FINISHED --2022-02-21 13:04:00--
Total wall clock time: 6m 28s
Downloaded: 35 files, 8.9G in 5m 39s (26.8 MB/s)


In [16]:
#Check directory for all files
!ls

12M_R1_val_1_5x.bedgraph 36F_R1_val_1_5x.bedgraph 54F_R1_val_1_5x.bedgraph
13M_R1_val_1_5x.bedgraph 39F_R1_val_1_5x.bedgraph 59M_R1_val_1_5x.bedgraph
16F_R1_val_1_5x.bedgraph 3F_R1_val_1_5x.bedgraph  64M_R1_val_1_5x.bedgraph
19F_R1_val_1_5x.bedgraph 41F_R1_val_1_5x.bedgraph 6M_R1_val_1_5x.bedgraph
22F_R1_val_1_5x.bedgraph 44F_R1_val_1_5x.bedgraph 76F_R1_val_1_5x.bedgraph
23M_R1_val_1_5x.bedgraph 48M_R1_val_1_5x.bedgraph 77F_R1_val_1_5x.bedgraph
29F_R1_val_1_5x.bedgraph 50F_R1_val_1_5x.bedgraph 7M_R1_val_1_5x.bedgraph
31M_R1_val_1_5x.bedgraph 52F_R1_val_1_5x.bedgraph 9M_R1_val_1_5x.bedgraph
35F_R1_val_1_5x.bedgraph 53F_R1_val_1_5x.bedgraph


In [15]:
#Obtain md5
!md5 *

MD5 (12M_R1_val_1_5x.bedgraph) = 2be3d2693ee2b983a98546fdb03ea7c4
MD5 (13M_R1_val_1_5x.bedgraph) = e11bce6266565305b96392d99dfc97e8
MD5 (16F_R1_val_1_5x.bedgraph) = 1b6587ea799136de40b08c6737c84c40
MD5 (19F_R1_val_1_5x.bedgraph) = f37e3564d37446ecdad0bc353e7c389f
MD5 (22F_R1_val_1_5x.bedgraph) = f3555e77e4148e61d749b2c2484d2991
MD5 (23M_R1_val_1_5x.bedgraph) = 510db373f75569ab6cbbfc95d01963bc
MD5 (29F_R1_val_1_5x.bedgraph) = 16a4229fc65000b14c3be02875243279
MD5 (31M_R1_val_1_5x.bedgraph) = dffadff27e431d84856d5eafa3ba330e
MD5 (35F_R1_val_1_5x.bedgraph) = f76ff82c606b28d97033e8582649c29f
MD5 (36F_R1_val_1_5x.bedgraph) = d05f9d0fbd7ddde77772f56cfe6745af
MD5 (39F_R1_val_1_5x.bedgraph) = c2ad5ea91c70896feb644e004b7acdc7
MD5 (3F_R1_val_1_5x.bedgraph) = fa42bb14f17ecf12aa94356fa83d4427
MD5 (41F_R1_val_1_5x.bedgraph) = cccecd107353fcc4e522a5840a54df0a
MD5 (44F_R1_val_1_5x.bedgraph) = bb61884d72c7a55a166976f1352143a9
MD5 (48M_R1_val_1_5x.bedgraph) = bea5502d6a7528fd6852ea1008b2ab32
MD5 (50F_R1

In [18]:
%%bash

for f in *5x.bedgraph
do
/opt/homebrew/bin/sortBed \
-i ${f} \
> $(basename ${f%_5x.bedgraph})_5x.sort.bedgraph
done

In [19]:
!ls *sort*

12M_R1_val_1_5x.sort.bedgraph 44F_R1_val_1_5x.sort.bedgraph
13M_R1_val_1_5x.sort.bedgraph 48M_R1_val_1_5x.sort.bedgraph
16F_R1_val_1_5x.sort.bedgraph 50F_R1_val_1_5x.sort.bedgraph
19F_R1_val_1_5x.sort.bedgraph 52F_R1_val_1_5x.sort.bedgraph
22F_R1_val_1_5x.sort.bedgraph 53F_R1_val_1_5x.sort.bedgraph
23M_R1_val_1_5x.sort.bedgraph 54F_R1_val_1_5x.sort.bedgraph
29F_R1_val_1_5x.sort.bedgraph 59M_R1_val_1_5x.sort.bedgraph
31M_R1_val_1_5x.sort.bedgraph 64M_R1_val_1_5x.sort.bedgraph
35F_R1_val_1_5x.sort.bedgraph 6M_R1_val_1_5x.sort.bedgraph
36F_R1_val_1_5x.sort.bedgraph 76F_R1_val_1_5x.sort.bedgraph
39F_R1_val_1_5x.sort.bedgraph 77F_R1_val_1_5x.sort.bedgraph
3F_R1_val_1_5x.sort.bedgraph  7M_R1_val_1_5x.sort.bedgraph
41F_R1_val_1_5x.sort.bedgraph 9M_R1_val_1_5x.sort.bedgraph


## 2. Concatenate percent methylation information

### 2a. Remove C->T SNPs

For each sample, I will use BS-Snper output to change the percent methylation for a C->T SNP to 0.

In [28]:
#Download 5x SNP
!wget -r \
--no-check-certificate --no-directories --no-parent --reject "index.html*" \
-P . \
-A "*vcf" https://gannet.fish.washington.edu/seashell/bu-github/nb-2022/C_virginica/analyses/bsnp01/

--2022-02-21 13:39:43--  https://gannet.fish.washington.edu/seashell/bu-github/nb-2022/C_virginica/analyses/bsnp01/
Resolving gannet.fish.washington.edu (gannet.fish.washington.edu)... 128.95.149.52
Connecting to gannet.fish.washington.edu (gannet.fish.washington.edu)|128.95.149.52|:443... connected.
  Unable to locally verify the issuer's authority.
HTTP request sent, awaiting response... 200 OK
Length: unspecified [text/html]
Saving to: ‘./index.html.tmp’

index.html.tmp          [ <=>                ]  32.59K  --.-KB/s    in 0.02s   

2022-02-21 13:39:45 (1.42 MB/s) - ‘./index.html.tmp’ saved [33377]

Loading robots.txt; please ignore errors.
--2022-02-21 13:39:45--  https://gannet.fish.washington.edu/robots.txt
Reusing existing connection to gannet.fish.washington.edu:443.
HTTP request sent, awaiting response... 404 Not Found
2022-02-21 13:39:45 ERROR 404: Not Found.

Removing ./index.html.tmp since it should be rejected.

--2022-02-21 13:39:45--  https://gannet.fish.washington.edu

HTTP request sent, awaiting response... 200 OK
Length: 537520139 (513M) [text/x-vcard]
Saving to: ‘./23M_R1_val_1_bismark_bt2_pe.SNP-results.vcf’

23M_R1_val_1_bismar 100%[===================>] 512.62M  33.3MB/s    in 15s     

2022-02-21 13:42:24 (33.2 MB/s) - ‘./23M_R1_val_1_bismark_bt2_pe.SNP-results.vcf’ saved [537520139/537520139]

--2022-02-21 13:42:24--  https://gannet.fish.washington.edu/seashell/bu-github/nb-2022/C_virginica/analyses/bsnp01/29F_R1_val_1_bismark_bt2_pe.SNP-results.vcf
Reusing existing connection to gannet.fish.washington.edu:443.
HTTP request sent, awaiting response... 200 OK
Length: 493305649 (470M) [text/x-vcard]
Saving to: ‘./29F_R1_val_1_bismark_bt2_pe.SNP-results.vcf’

29F_R1_val_1_bismar 100%[===================>] 470.45M  33.5MB/s    in 14s     

2022-02-21 13:42:38 (33.2 MB/s) - ‘./29F_R1_val_1_bismark_bt2_pe.SNP-results.vcf’ saved [493305649/493305649]

--2022-02-21 13:42:38--  https://gannet.fish.washington.edu/seashell/bu-github/nb-2022/C_virginica/a

HTTP request sent, awaiting response... 200 OK
Length: 495489563 (473M) [text/x-vcard]
Saving to: ‘./76F_R1_val_1_bismark_bt2_pe.SNP-results.vcf’

76F_R1_val_1_bismar 100%[===================>] 472.54M  33.5MB/s    in 14s     

2022-02-21 13:46:08 (33.2 MB/s) - ‘./76F_R1_val_1_bismark_bt2_pe.SNP-results.vcf’ saved [495489563/495489563]

--2022-02-21 13:46:08--  https://gannet.fish.washington.edu/seashell/bu-github/nb-2022/C_virginica/analyses/bsnp01/77F_R1_val_1_bismark_bt2_pe.SNP-results.vcf
Reusing existing connection to gannet.fish.washington.edu:443.
HTTP request sent, awaiting response... 200 OK
Length: 518615965 (495M) [text/x-vcard]
Saving to: ‘./77F_R1_val_1_bismark_bt2_pe.SNP-results.vcf’

77F_R1_val_1_bismar 100%[===================>] 494.59M  32.6MB/s    in 15s     

2022-02-21 13:46:23 (32.1 MB/s) - ‘./77F_R1_val_1_bismark_bt2_pe.SNP-results.vcf’ saved [518615965/518615965]

--2022-02-21 13:46:23--  https://gannet.fish.washington.edu/seashell/bu-github/nb-2022/C_virginica/a

In [40]:
!{bedtoolsDirectory}intersectBed \
-u \
-a 3F_R1_val_1_bismark_bt2_pe.SNP-results.vcf \
-b 3F_R1_val_1_5x.sort.bedgraph \
| grep "C	T" | head

NC_035780.1	32910	.	C	T	1000	PASS	DP=23;ADF=0,0;ADR=0,23;AD=0,23;	GT:DP:ADF:ADR:AD:BSD:BSQ:ALFR	0/1:23:0,0:0,23:0,23:0,0,21,0,0,23,0,0:0,0,37,0,0,36,0,0:0.000,1.000
NC_035780.1	80703	.	C	T	1000	PASS	DP=23;ADF=0,0;ADR=0,23;AD=0,23;	GT:DP:ADF:ADR:AD:BSD:BSQ:ALFR	0/1:23:0,0:0,23:0,23:0,0,10,0,0,23,0,0:0,0,36,0,0,36,0,0:0.000,1.000
NC_035780.1	89426	.	C	T	4	Low	DP=1;ADF=0,0;ADR=0,1;AD=0,1;	GT:DP:ADF:ADR:AD:BSD:BSQ:ALFR	1/1:1:0,0:0,1:0,1:0,0,0,0,0,1,0,0:0,0,0,0,0,37,0,0:0.000,1.000
NC_035780.1	90833	.	C	T	1000	PASS	DP=20;ADF=0,0;ADR=0,20;AD=0,20;	GT:DP:ADF:ADR:AD:BSD:BSQ:ALFR	0/1:20:0,0:0,20:0,20:0,0,36,0,0,20,0,0:0,0,37,0,0,36,0,0:0.000,1.000
NC_035780.1	109517	.	C	T	1000	PASS	DP=17;ADF=0,0;ADR=0,17;AD=0,17;	GT:DP:ADF:ADR:AD:BSD:BSQ:ALFR	0/1:17:0,0:0,17:0,17:0,0,29,0,0,17,0,0:0,0,37,0,0,36,0,0:0.000,1.000
NC_035780.1	110152	.	C	T	1000	PASS	DP=30;ADF=0,0;ADR=2,28;AD=2,28;	GT:DP:ADF:ADR:AD:BSD:BSQ:ALFR	0/1:30:0,0:2,28:2,28:0,0,12,0,0,28,2,0:0,0,35,0,0,37,37,0:0.067,0.933
NC_035780.1	124935	.

### 2b. Create a union BEDgraph

I will use `unionBedGraphs` to concatenate information for all loci across samples.

In [12]:
bedtoolsDirectory = "/opt/homebrew/bin/"

In [13]:
!{bedtoolsDirectory}unionBedGraphs -h


Tool:    bedtools unionbedg (aka unionBedGraphs)
Version: v2.30.0
Summary: Combines multiple BedGraph files into a single file,
	 allowing coverage comparisons between them.

Usage:   bedtools unionbedg [OPTIONS] -i FILE1 FILE2 .. FILEn
	 Assumes that each BedGraph file is sorted by chrom/start 
	 and that the intervals in each are non-overlapping.

Options: 
	-header		Print a header line.
			(chrom/start/end + names of each file).

	-names		A list of names (one/file) to describe each file in -i.
			These names will be printed in the header line.

	-g		Use genome file to calculate empty regions.
			- STRING.

	-empty		Report empty regions (i.e., start/end intervals w/o
			values in all files).
			- Requires the '-g FILE' parameter.

	-filler TEXT	Use TEXT when representing intervals having no value.
			- Default is '0', but you can use 'N/A' or any text.

	-examples	Show detailed usage examples.



In [20]:
#Create union BEDgraph from sorted files
#Include a header
#Use N/A when there is no data for a CpG in a sample
#Define sample IDs
#Use sorted bedgraphs
#Save output
!{bedtoolsDirectory}unionBedGraphs \
-header \
-filler N/A \
-names 12 13 16 19 22 23 29 31 35 36 39 3 41 44 48 50 52 53 54 59 64 6 76 77 7 9 \
-i \
*5x.sort.bedgraph \
> union_5x.bedgraph

In [21]:
#Check output
!head union_5x.bedgraph
!wc -l union_5x.bedgraph

chrom	start	end	12	13	16	19	22	23	29	31	35	36	39	3	41	44	48	50	52	53	54	59	64	6	76	77	7	9
NC_007175.2	48	50	0.000000	0.000000	1.923077	0.731452	1.015228	0.000000	1.444623	3.125000	0.844511	1.699182	0.541339	1.694915	1.928375	2.136076	1.086957	1.672640	1.806240	1.100917	1.780694	0.000000	3.973510	0.653595	0.682057	1.661475	3.750000	1.754386
NC_007175.2	50	52	0.000000	0.000000	1.626016	0.733855	1.507937	0.000000	1.349325	1.470588	0.600462	1.700880	0.599908	1.500000	2.570694	1.327434	1.036269	1.874311	1.371951	1.069218	1.842105	0.000000	3.797468	0.632911	0.442478	1.439539	3.488372	1.666667
NC_007175.2	87	89	1.169591	1.293103	1.045857	0.286907	0.789771	0.990099	0.859599	0.671141	0.666349	0.813008	0.444115	1.284875	0.800915	1.361796	0.245700	0.959596	0.852273	0.758853	0.866927	0.000000	0.319489	0.666667	0.208008	1.021477	0.478469	0.000000
NC_007175.2	146	148	1.261830	0.461894	1.502146	0.684369	1.081187	0.819672	1.183206	0.332226	0.721028	1.522344	0.562023	0.995025	1.548541	1.321760	0.383142

### 2b. Manipulate with `pandas`

In [22]:
#Import union data into pandas
#Check head
df = pd.read_table("union_5x.bedgraph")
df.head(5)

chrom  start  end        12        13        16        19        22  \
0  NC_007175.2     48   50  0.000000  0.000000  1.923077  0.731452  1.015228   
1  NC_007175.2     50   52  0.000000  0.000000  1.626016  0.733855  1.507937   
2  NC_007175.2     87   89  1.169591  1.293103  1.045857  0.286907  0.789771   
3  NC_007175.2    146  148  1.261830  0.461894  1.502146  0.684369  1.081187   
4  NC_007175.2    192  194  1.129944  1.271186  1.726908  0.691776  1.094563   

         23        29  ...        52        53        54       59        64  \
0  0.000000  1.444623  ...  1.806240  1.100917  1.780694  0.00000  3.973510   
1  0.000000  1.349325  ...  1.371951  1.069218  1.842105  0.00000  3.797468   
2  0.990099  0.859599  ...  0.852273  0.758853  0.866927  0.00000  0.319489   
3  0.819672  1.183206  ...  1.306458  1.210914  0.924855  0.00000  2.027027   
4  1.955990  1.097734  ...  1.486346  1.194200  0.896287  0.47619  1.369863   

          6        76        77         7         9  
0  0.653595  0.682057  1.661475  3.750000  1.754386  
1  0.632911  0.442478  1.439539  3.488372  1.666667  
2  0.666667  0.208008  1.021477  0.478469  0.000000  
3  0.702988  0.475325  1.308017  1.566580  0.456621  
4  0.161031  0.558659  1.286383  2.195122  0.840336  

[5 rows x 29 columns]

In [23]:
#Average all samples for total genome methylation information and save as a new column
#NA are not included in averages
#Check output
df['total'] = df[['12', '13', '16', '19', '22', '23', '29', '31', '35', '36', '39', '3', '41', '44', '48', '50', '52', '53', '54', '59', '64', '6', '76', '77', '7', '9']].mean(axis=1)
df.tail(10)

chrom     start       end   12   13   16  19   22  23   29  \
13563069  NC_035789.1  32649732  32649734  0.0  0.0  0.0 NaN  NaN NaN  0.0   
13563070  NC_035789.1  32649736  32649738  0.0  0.0  0.0 NaN  NaN NaN  0.0   
13563071  NC_035789.1  32649799  32649801  NaN  0.0  NaN NaN  NaN NaN  NaN   
13563072  NC_035789.1  32649876  32649878  0.0  0.0  0.0 NaN  0.0 NaN  0.0   
13563073  NC_035789.1  32649885  32649887  0.0  0.0  0.0 NaN  0.0 NaN  0.0   
13563074  NC_035789.1  32649895  32649897  0.0  0.0  0.0 NaN  0.0 NaN  0.0   
13563075  NC_035789.1  32649930  32649932  0.0  0.0  0.0 NaN  0.0 NaN  0.0   
13563076  NC_035789.1  32649933  32649935  0.0  0.0  0.0 NaN  0.0 NaN  0.0   
13563077  NC_035789.1  32649966  32649968  0.0  0.0  0.0 NaN  0.0 NaN  0.0   
13563078  NC_035789.1  32650035  32650037  NaN  NaN  NaN NaN  NaN NaN  NaN   

          ...   53   54   59   64    6   76   77    7   9     total  
13563069  ...  0.0  NaN  0.0  NaN  0.0  0.0  0.0  0.0 NaN  0.000000  
13563070  ...  0.0  NaN  0.0  NaN  0.0  0.0  0.0  0.0 NaN  0.000000  
13563071  ...  NaN  0.0  NaN  NaN  NaN  NaN  NaN  NaN NaN  0.000000  
13563072  ...  NaN  0.0  0.0  NaN  0.0  0.0  0.0  0.0 NaN  0.000000  
13563073  ...  NaN  0.0  0.0  0.0  0.0  0.0  0.0  0.0 NaN  0.000000  
13563074  ...  NaN  0.0  0.0  0.0  0.0  0.0  0.0  0.0 NaN  0.000000  
13563075  ...  NaN  0.0  0.0  0.0  0.0  0.0  0.0  0.0 NaN  0.000000  
13563076  ...  NaN  0.0  0.0  0.0  0.0  0.0  0.0  0.0 NaN  0.000000  
13563077  ...  NaN  0.0  0.0  0.0  0.0  0.0  0.0  NaN NaN  1.020408  
13563078  ...  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN NaN  0.000000  

[10 rows x 30 columns]

In [26]:
#Save dataframe in a tabular format and include N/As. Do not include quotes.
df.to_csv("union-averages.bedgraph", sep = "\t", na_rep = "N/A", quoting = 3)

In [27]:
#Check pandas manipulations
!tail union-averages.bedgraph

13563069	NC_035789.1	32649732	32649734	0.0	0.0	0.0	N/A	N/A	N/A	0.0	N/A	0.0	0.0	N/A	0.0	0.0	N/A	0.0	0.0	N/A	0.0	N/A	0.0	N/A	0.0	0.0	0.0	0.0	N/A	0.0
13563070	NC_035789.1	32649736	32649738	0.0	0.0	0.0	N/A	N/A	N/A	0.0	N/A	0.0	0.0	N/A	0.0	0.0	N/A	0.0	0.0	N/A	0.0	N/A	0.0	N/A	0.0	0.0	0.0	0.0	N/A	0.0
13563071	NC_035789.1	32649799	32649801	N/A	0.0	N/A	N/A	N/A	N/A	N/A	N/A	0.0	N/A	N/A	0.0	N/A	N/A	N/A	N/A	N/A	N/A	0.0	N/A	N/A	N/A	N/A	N/A	N/A	N/A	0.0
13563072	NC_035789.1	32649876	32649878	0.0	0.0	0.0	N/A	0.0	N/A	0.0	N/A	0.0	0.0	N/A	0.0	N/A	N/A	0.0	0.0	0.0	N/A	0.0	0.0	N/A	0.0	0.0	0.0	0.0	N/A	0.0
13563073	NC_035789.1	32649885	32649887	0.0	0.0	0.0	N/A	0.0	N/A	0.0	N/A	0.0	0.0	N/A	0.0	N/A	N/A	N/A	0.0	0.0	N/A	0.0	0.0	0.0	0.0	0.0	0.0	0.0	N/A	0.0
13563074	NC_035789.1	32649895	32649897	0.0	0.0	0.0	N/A	0.0	N/A	0.0	N/A	0.0	0.0	N/A	0.0	N/A	N/A	N/A	0.0	0.0	N/A	0.0	0.0	0.0	0.0	0.0	0.0	0.0	N/A	0.0
13563075	NC_035789.1	32649930	32649932	0.0	0.0	0.0	N/A	0.0	N/A	0.0	N/A	0.0	0.0	N/A	0.0	N/A	N/A	N/A	0.0	0.0	N/A	0.0	0.0

## 3. Characterize methylation for each CpG dinucleotude

- methylated: ≥ 50%
- sparsely methylated: 10-50%
- unmethylated: ≤ 10%

In [7]:
#8 individual sample files + 1 union bedgraph
#Count lines
!find zr3616*5x.bedgraph
!wc -l zr3616*5x.bedgraph

zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph
zr3616_2_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph
zr3616_3_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph
zr3616_4_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph
zr3616_5_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph
zr3616_6_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph
zr3616_7_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph
zr3616_8_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph
zr3616_union-averages_5x.bedgraph
 8422611 zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph
 8468611 zr3616_2_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph
 8384664 zr3616_3_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph
 8689568 zr3616_4_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph
 8062541 zr3616_5_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph
 8471405 zr3616_6_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph
 8225132 zr3616_7_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph
 8316308 zr3616_8_R1_val_1_val_1_

In [10]:
%%bash

for f in zr3616*5x.bedgraph
do
/opt/homebrew/bin/subtractBed \
-a ${f} \
-b /Volumes/web/spartina/project-gigas-oa-meth/output/BS-Snper/unique-CT-SNPs.bed \
> ${f}.NO-SNPs
done

In [11]:
#Count lines of files with no SNP information
!find *NO-SNPs
!wc -l *NO-SNPs

zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs
zr3616_2_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs
zr3616_3_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs
zr3616_4_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs
zr3616_5_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs
zr3616_6_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs
zr3616_7_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs
zr3616_8_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs
zr3616_union-averages_5x.bedgraph.NO-SNPs
 8148908 zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs
 8193942 zr3616_2_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs
 8110578 zr3616_3_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs
 8412899 zr3616_4_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs
 7793250 zr3616_5_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs
 8196826 zr3616_6_R1_val_1_val_1_val_1_bismark_bt2_pe._

### 3b. Methylated loci

In [12]:
%%bash
for f in zr3616*NO-SNPs
do
    awk '{if ($4 >= 50) { print $1, $2, $3, $4 }}' ${f} \
    > ${f}-Meth
done

In [13]:
!head *-Meth

==> zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth <==
NC_047559.1 1547 1549 100.000000
NC_047559.1 1571 1573 87.500000
NC_047559.1 2267 2269 100.000000
NC_047559.1 2291 2293 100.000000
NC_047559.1 4073 4075 60.000000
NC_047559.1 4791 4793 64.705882
NC_047559.1 4835 4837 88.235294
NC_047559.1 4843 4845 81.250000
NC_047559.1 5605 5607 60.000000
NC_047559.1 5613 5615 66.666667

==> zr3616_2_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth <==
NC_047559.1 1571 1573 83.333333
NC_047559.1 2267 2269 100.000000
NC_047559.1 2291 2293 100.000000
NC_047559.1 2448 2450 100.000000
NC_047559.1 2988 2990 81.818182
NC_047559.1 3902 3904 57.142857
NC_047559.1 3916 3918 100.000000
NC_047559.1 4073 4075 90.909091
NC_047559.1 4270 4272 57.142857
NC_047559.1 4791 4793 71.428571

==> zr3616_3_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth <==
NC_047559.1 1571 1573 100.000000
NC_047559.1 2291 2293 100.000000
NC_047559.1 2448 2450 100.000000
NC_047559.1 298

In [14]:
!wc -l *-Meth

  852626 zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth
  840818 zr3616_2_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth
  861662 zr3616_3_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth
  891492 zr3616_4_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth
  808582 zr3616_5_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth
  844274 zr3616_6_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth
  891718 zr3616_7_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth
  837432 zr3616_8_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth
  966655 zr3616_union-averages_5x.bedgraph.NO-SNPs-Meth
 7795259 total


In [15]:
#Get line counts for each fine
# Remove 10th line (total entries)
#Ensure output is tab-delimited
#Save output
!wc -l *-Meth \
| sed '10,$ d' \
| awk '{print $1"\t"$2}' \
> zr3616_5x-Meth-counts.txt

In [16]:
!head zr3616_5x-Meth-counts.txt

852626	zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth
840818	zr3616_2_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth
861662	zr3616_3_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth
891492	zr3616_4_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth
808582	zr3616_5_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth
844274	zr3616_6_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth
891718	zr3616_7_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth
837432	zr3616_8_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth
966655	zr3616_union-averages_5x.bedgraph.NO-SNPs-Meth


### 3c. Sparsely methylated loci

In [17]:
%%bash
for f in zr3616*NO-SNPs
do
    awk '{if ($4 < 50) { print $1, $2, $3, $4}}' ${f} \
    | awk '{if ($4 > 10) { print $1, $2, $3, $4 }}' \
    > ${f}-sparseMeth
done

In [18]:
!head *-sparseMeth

==> zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth <==
NC_047559.1 4887 4889 20.000000
NC_047559.1 4909 4911 33.333333
NC_047559.1 5500 5502 25.000000
NC_047559.1 7716 7718 40.000000
NC_047559.1 7814 7816 47.058824
NC_047559.1 9237 9239 29.166667
NC_047559.1 9658 9660 37.500000
NC_047559.1 9661 9663 22.222222
NC_047559.1 10899 10901 12.195122
NC_047559.1 18234 18236 11.111111

==> zr3616_2_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth <==
NC_001276.1 4444 4446 14.285714
NC_047559.1 4397 4399 47.058824
NC_047559.1 4909 4911 42.857143
NC_047559.1 5605 5607 42.857143
NC_047559.1 5613 5615 37.500000
NC_047559.1 7716 7718 20.000000
NC_047559.1 7850 7852 40.000000
NC_047559.1 8970 8972 11.111111
NC_047559.1 8979 8981 14.285714
NC_047559.1 9658 9660 33.333333

==> zr3616_3_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth <==
NC_047559.1 4073 4075 42.857143
NC_047559.1 8970 8972 25.000000
NC_047559.1 8979 8981 11.111111
NC_

In [19]:
!wc -l *-sparseMeth

  651862 zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth
  654311 zr3616_2_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth
  622053 zr3616_3_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth
  668946 zr3616_4_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth
  594948 zr3616_5_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth
  645242 zr3616_6_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth
  594427 zr3616_7_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth
  634990 zr3616_8_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth
  954751 zr3616_union-averages_5x.bedgraph.NO-SNPs-sparseMeth
 6021530 total


In [20]:
#Get line counts for each fine
# Remove 10th line (total entries)
#Ensure output is tab-delimited
#Save output
!wc -l *-sparseMeth \
| sed '10,$ d' \
| awk '{print $1"\t"$2}' \
> zr3616_5x-sparseMeth-counts.txt

In [21]:
!head zr3616_5x-sparseMeth-counts.txt

651862	zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth
654311	zr3616_2_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth
622053	zr3616_3_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth
668946	zr3616_4_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth
594948	zr3616_5_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth
645242	zr3616_6_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth
594427	zr3616_7_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth
634990	zr3616_8_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth
954751	zr3616_union-averages_5x.bedgraph.NO-SNPs-sparseMeth


### 3d. Unmethylated loci

In [22]:
%%bash
for f in zr3616*NO-SNPs
do
    awk '{if ($4 <= 10) { print $1, $2, $3, $4 }}' ${f} \
    > ${f}-unMeth
done

In [23]:
!head *-unMeth

==> zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth <==
NC_001276.1 34 36 0.000000
NC_001276.1 123 125 0.531915
NC_001276.1 305 307 0.313480
NC_001276.1 433 435 0.243112
NC_001276.1 457 459 0.148368
NC_001276.1 482 484 0.409500
NC_001276.1 609 611 0.072993
NC_001276.1 781 783 0.330852
NC_001276.1 826 828 0.435540
NC_001276.1 951 953 0.305499

==> zr3616_2_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth <==
NC_001276.1 34 36 1.672241
NC_001276.1 123 125 0.582751
NC_001276.1 305 307 0.303490
NC_001276.1 433 435 0.106496
NC_001276.1 457 459 0.476644
NC_001276.1 482 484 0.418848
NC_001276.1 609 611 0.484966
NC_001276.1 781 783 0.209644
NC_001276.1 826 828 0.226757
NC_001276.1 951 953 0.276243

==> zr3616_3_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth <==
NC_001276.1 34 36 0.000000
NC_001276.1 123 125 0.218579
NC_001276.1 305 307 0.344828
NC_001276.1 433 435 0.207900
NC_001276.1 457 459 0.191022
NC_001276.1 482 484 0.110619
NC_0012

In [24]:
!wc -l *-unMeth

 6644420 zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth
 6698813 zr3616_2_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth
 6626863 zr3616_3_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth
 6852461 zr3616_4_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth
 6389720 zr3616_5_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth
 6707310 zr3616_6_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth
 6466724 zr3616_7_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth
 6571561 zr3616_8_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth
 9018512 zr3616_union-averages_5x.bedgraph.NO-SNPs-unMeth
 61976384 total


In [25]:
#Get line counts for each fine
# Remove 10th line (total entries)
#Ensure output is tab-delimited
#Save output
!wc -l *-unMeth \
| sed '10,$ d' \
| awk '{print $1"\t"$2}' \
> zr3616_5x-unMeth-counts.txt

In [26]:
!head zr3616_5x-unMeth-counts.txt

6644420	zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth
6698813	zr3616_2_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth
6626863	zr3616_3_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth
6852461	zr3616_4_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth
6389720	zr3616_5_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth
6707310	zr3616_6_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth
6466724	zr3616_7_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth
6571561	zr3616_8_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth
9018512	zr3616_union-averages_5x.bedgraph.NO-SNPs-unMeth


## 4. Characterize genomic location of CpGs

I will identify overlaps between CpG loci (methylated, sparsely methylated, unmethylated) and various genome feature tracks:

- gene
- exon UTR
- CDS
- intron
- upstream flanks
- downstream flanks
- intergenic regions
- lncRNA
- transposable elements

Since the exon track = exon UTR + CDS, and mRNA = exon + intron, I will not need to use those tracks separately.

In [31]:
#9 file types (8 samples + 1 union), 3 files per type (Meth, sparseMeth, unMeth) = 27 total
!find zr3616*5x.bedgraph*SNPs-*
!find zr3616*5x.bedgraph*SNPs-* | wc -l

zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth
zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth
zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth
zr3616_2_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth
zr3616_2_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth
zr3616_2_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth
zr3616_3_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth
zr3616_3_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth
zr3616_3_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth
zr3616_4_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth
zr3616_4_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth
zr3616_4_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth
zr3616_5_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth
zr3616_5_R1_val_1_val_1_val_1_bismark_bt2_pe.

In [32]:
%%bash

for f in zr3616*5x.bedgraph*SNPs-*
do
    awk '{print $1"\t"$2"\t"$3}' ${f} > ${f}.bed
    wc -l ${f}.bed
done

  852626 zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth.bed
  651862 zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth.bed
 6644420 zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth.bed
  840818 zr3616_2_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth.bed
  654311 zr3616_2_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth.bed
 6698813 zr3616_2_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth.bed
  861662 zr3616_3_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth.bed
  622053 zr3616_3_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth.bed
 6626863 zr3616_3_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth.bed
  891492 zr3616_4_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth.bed
  668946 zr3616_4_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth.bed
 6852461 zr3616_4_R1_val_1_val_1_val_1_bismark

In [33]:
!find *bed

zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth.bed
zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth.bed
zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth.bed
zr3616_2_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth.bed
zr3616_2_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth.bed
zr3616_2_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth.bed
zr3616_3_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth.bed
zr3616_3_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth.bed
zr3616_3_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth.bed
zr3616_4_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth.bed
zr3616_4_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth.bed
zr3616_4_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth.bed
zr3616_5_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Me

### 4b. Gene

In [9]:
#Get overlaps between CpG background and genes for downstream annotation

!{bedtoolsDirectory}intersectBed \
-wb \
-a zr3616_union-averages_5x.bedgraph.bed \
-b ../../genome-feature-files/cgigas_uk_roslin_v1_gene.gff \
> zr3616_union-averages_5x-Gene-wb.bed
!head zr3616_union-averages_5x-Gene-wb.bed
!wc -l zr3616_union-averages_5x-Gene-wb.bed

NC_047559.1	10155	10157	NC_047559.1	Gnomon	gene	9839	11386	.	+	.	ID=gene-LOC117693020;Dbxref=GeneID:117693020;Name=LOC117693020;gbkey=Gene;gene=LOC117693020;gene_biotype=lncRNA
NC_047559.1	10215	10217	NC_047559.1	Gnomon	gene	9839	11386	.	+	.	ID=gene-LOC117693020;Dbxref=GeneID:117693020;Name=LOC117693020;gbkey=Gene;gene=LOC117693020;gene_biotype=lncRNA
NC_047559.1	10270	10272	NC_047559.1	Gnomon	gene	9839	11386	.	+	.	ID=gene-LOC117693020;Dbxref=GeneID:117693020;Name=LOC117693020;gbkey=Gene;gene=LOC117693020;gene_biotype=lncRNA
NC_047559.1	10292	10294	NC_047559.1	Gnomon	gene	9839	11386	.	+	.	ID=gene-LOC117693020;Dbxref=GeneID:117693020;Name=LOC117693020;gbkey=Gene;gene=LOC117693020;gene_biotype=lncRNA
NC_047559.1	10314	10316	NC_047559.1	Gnomon	gene	9839	11386	.	+	.	ID=gene-LOC117693020;Dbxref=GeneID:117693020;Name=LOC117693020;gbkey=Gene;gene=LOC117693020;gene_biotype=lncRNA
NC_047559.1	10358	10360	NC_047559.1	Gnomon	gene	9839	11386	.	+	.	ID=gene-LOC117693020;Dbxref=GeneID:117693020;Name=

In [34]:
%%bash
for f in *bed
do
    /opt/homebrew/bin/intersectBed \
    -u \
    -a ${f} \
    -b ../../genome-feature-files/cgigas_uk_roslin_v1_gene.gff \
    > ${f}-Gene
done

In [35]:
#Check output
!head *Gene

==> zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth.bed-Gene <==
NC_047559.1	360322	360324
NC_047559.1	360361	360363
NC_047559.1	361347	361349
NC_047559.1	364329	364331
NC_047559.1	375341	375343
NC_047559.1	375360	375362
NC_047559.1	376111	376113
NC_047559.1	376170	376172
NC_047559.1	376962	376964
NC_047559.1	377335	377337

==> zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth.bed-Gene <==
NC_047559.1	10899	10901
NC_047559.1	18234	18236
NC_047559.1	61081	61083
NC_047559.1	68070	68072
NC_047559.1	100249	100251
NC_047559.1	100276	100278
NC_047559.1	100305	100307
NC_047559.1	100319	100321
NC_047559.1	100440	100442
NC_047559.1	100454	100456

==> zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth.bed-Gene <==
NC_047559.1	10270	10272
NC_047559.1	10292	10294
NC_047559.1	10314	10316
NC_047559.1	10358	10360
NC_047559.1	10380	10382
NC_047559.1	10391	10393
NC_047559.1	10402	10404
NC_047559.1	10413	10415
NC_047559.1	10457	1045


==> zr3616_union-averages_5x.bedgraph.NO-SNPs-sparseMeth.bed-Gene <==
NC_047559.1	60313	60315
NC_047559.1	60371	60373
NC_047559.1	60492	60494
NC_047559.1	61081	61083
NC_047559.1	62078	62080
NC_047559.1	62234	62236
NC_047559.1	63068	63070
NC_047559.1	63072	63074
NC_047559.1	63078	63080
NC_047559.1	64815	64817

==> zr3616_union-averages_5x.bedgraph.NO-SNPs-unMeth.bed-Gene <==
NC_047559.1	10155	10157
NC_047559.1	10215	10217
NC_047559.1	10270	10272
NC_047559.1	10292	10294
NC_047559.1	10314	10316
NC_047559.1	10358	10360
NC_047559.1	10380	10382
NC_047559.1	10391	10393
NC_047559.1	10402	10404
NC_047559.1	10413	10415


In [36]:
#Count number of overlaps
!wc -l *Gene

  793356 zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth.bed-Gene
  456348 zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth.bed-Gene
 3615169 zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth.bed-Gene
  780836 zr3616_2_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth.bed-Gene
  454638 zr3616_2_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth.bed-Gene
 3648886 zr3616_2_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth.bed-Gene
  800933 zr3616_3_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth.bed-Gene
  432941 zr3616_3_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth.bed-Gene
 3613729 zr3616_3_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth.bed-Gene
  828225 zr3616_4_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth.bed-Gene
  463701 zr3616_4_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth.

In [37]:
#Get line counts for each fine
# Remove 28th line (total entries)
#Ensure output is tab-delimited
#Save output
!wc -l *-Gene \
| sed '28,$ d' \
| awk '{print $1"\t"$2}' \
> zr3616_5x-Gene-counts.txt

### 4c. CDS

In [40]:
%%bash
for f in *bed
do
    /opt/homebrew/bin/intersectBed \
    -u \
    -a ${f} \
    -b ../../genome-feature-files/cgigas_uk_roslin_v1_CDS.gff \
    > ${f}-CDS
done

In [41]:
#Check output
!head *CDS

==> zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth.bed-CDS <==
NC_047559.1	432531	432533
NC_047559.1	432606	432608
NC_047559.1	433203	433205
NC_047559.1	433271	433273
NC_047559.1	545968	545970
NC_047559.1	548186	548188
NC_047559.1	548188	548190
NC_047559.1	548918	548920
NC_047559.1	549827	549829
NC_047559.1	549832	549834

==> zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth.bed-CDS <==
NC_047559.1	177876	177878
NC_047559.1	337616	337618
NC_047559.1	337639	337641
NC_047559.1	338662	338664
NC_047559.1	338708	338710
NC_047559.1	338753	338755
NC_047559.1	338777	338779
NC_047559.1	338819	338821
NC_047559.1	338862	338864
NC_047559.1	432696	432698

==> zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth.bed-CDS <==
NC_047559.1	14862	14864
NC_047559.1	15162	15164
NC_047559.1	15194	15196
NC_047559.1	15204	15206
NC_047559.1	15291	15293
NC_047559.1	15293	15295
NC_047559.1	15336	15338
NC_047559.1	15338	15340
NC_047559.1	15357


==> zr3616_union-averages_5x.bedgraph.NO-SNPs-Meth.bed-CDS <==
NC_047559.1	140284	140286
NC_047559.1	140286	140288
NC_047559.1	432531	432533
NC_047559.1	432606	432608
NC_047559.1	432670	432672
NC_047559.1	432696	432698
NC_047559.1	433203	433205
NC_047559.1	433271	433273
NC_047559.1	545968	545970
NC_047559.1	548148	548150

==> zr3616_union-averages_5x.bedgraph.NO-SNPs-sparseMeth.bed-CDS <==
NC_047559.1	140131	140133
NC_047559.1	140139	140141
NC_047559.1	140172	140174
NC_047559.1	140209	140211
NC_047559.1	140241	140243
NC_047559.1	140257	140259
NC_047559.1	140292	140294
NC_047559.1	140295	140297
NC_047559.1	140334	140336
NC_047559.1	140381	140383

==> zr3616_union-averages_5x.bedgraph.NO-SNPs-unMeth.bed-CDS <==
NC_047559.1	14862	14864
NC_047559.1	15099	15101
NC_047559.1	15162	15164
NC_047559.1	15194	15196
NC_047559.1	15204	15206
NC_047559.1	15291	15293
NC_047559.1	15293	15295
NC_047559.1	15336	15338
NC_047559.1	15338	15340
NC_047559.1	15357	15359


In [42]:
#Count number of overlaps
!wc -l *CDS

  305690 zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth.bed-CDS
   62303 zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth.bed-CDS
  829997 zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth.bed-CDS
  304850 zr3616_2_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth.bed-CDS
   63217 zr3616_2_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth.bed-CDS
  827906 zr3616_2_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth.bed-CDS
  310883 zr3616_3_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth.bed-CDS
   55085 zr3616_3_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth.bed-CDS
  826079 zr3616_3_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth.bed-CDS
  313947 zr3616_4_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth.bed-CDS
   58402 zr3616_4_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth.bed-CDS
  

In [43]:
#Get line counts for each fine
# Remove 28th line (total entries)
#Ensure output is tab-delimited
#Save output
!wc -l *-CDS \
| sed '28,$ d' \
| awk '{print $1"\t"$2}' \
> zr3616_5x-CDS-counts.txt

### 4d. Exon UTR

In [44]:
%%bash
for f in *bed
do
    /opt/homebrew/bin/intersectBed \
    -u \
    -a ${f} \
    -b ../../genome-feature-files/cgigas_uk_roslin_v1_exonUTR.gff \
    > ${f}-exonUTR
done

In [45]:
#Check output
!head *exonUTR

==> zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth.bed-exonUTR <==
NC_047559.1	545229	545231
NC_047559.1	545256	545258
NC_047559.1	571906	571908
NC_047559.1	571929	571931
NC_047559.1	572049	572051
NC_047559.1	572233	572235
NC_047559.1	572245	572247
NC_047559.1	572263	572265
NC_047559.1	572453	572455
NC_047559.1	572557	572559

==> zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth.bed-exonUTR <==
NC_047559.1	10899	10901
NC_047559.1	431124	431126
NC_047559.1	431205	431207
NC_047559.1	545687	545689
NC_047559.1	571583	571585
NC_047559.1	571838	571840
NC_047559.1	572075	572077
NC_047559.1	572153	572155
NC_047559.1	572367	572369
NC_047559.1	572615	572617

==> zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth.bed-exonUTR <==
NC_047559.1	10920	10922
NC_047559.1	10950	10952
NC_047559.1	11000	11002
NC_047559.1	11026	11028
NC_047559.1	14214	14216
NC_047559.1	14232	14234
NC_047559.1	14243	14245
NC_047559.1	14259	14261
NC_0475


==> zr3616_union-averages_5x.bedgraph.NO-SNPs-Meth.bed-exonUTR <==
NC_047559.1	418038	418040
NC_047559.1	418118	418120
NC_047559.1	418153	418155
NC_047559.1	418166	418168
NC_047559.1	418179	418181
NC_047559.1	431124	431126
NC_047559.1	545256	545258
NC_047559.1	571583	571585
NC_047559.1	571838	571840
NC_047559.1	571906	571908

==> zr3616_union-averages_5x.bedgraph.NO-SNPs-sparseMeth.bed-exonUTR <==
NC_047559.1	62234	62236
NC_047559.1	343574	343576
NC_047559.1	343603	343605
NC_047559.1	372095	372097
NC_047559.1	415945	415947
NC_047559.1	415975	415977
NC_047559.1	415998	416000
NC_047559.1	416071	416073
NC_047559.1	416078	416080
NC_047559.1	416088	416090

==> zr3616_union-averages_5x.bedgraph.NO-SNPs-unMeth.bed-exonUTR <==
NC_047559.1	10899	10901
NC_047559.1	10920	10922
NC_047559.1	10950	10952
NC_047559.1	11000	11002
NC_047559.1	11026	11028
NC_047559.1	11080	11082
NC_047559.1	14214	14216
NC_047559.1	14232	14234
NC_047559.1	14243	14245
NC_047559.1	14259	14261


In [46]:
#Count number of overlaps
!wc -l *exonUTR

   48945 zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth.bed-exonUTR
   32728 zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth.bed-exonUTR
  422149 zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth.bed-exonUTR
   46369 zr3616_2_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth.bed-exonUTR
   32998 zr3616_2_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth.bed-exonUTR
  427078 zr3616_2_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth.bed-exonUTR
   49947 zr3616_3_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth.bed-exonUTR
   31460 zr3616_3_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth.bed-exonUTR
  422437 zr3616_3_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth.bed-exonUTR
   51903 zr3616_4_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth.bed-exonUTR
   33259 zr3616_4_R1_val_1_val_1_val_1_bismark_bt2_pe._5

In [47]:
#Get line counts for each fine
# Remove 28th line (total entries)
#Ensure output is tab-delimited
#Save output
!wc -l *-exonUTR \
| sed '28,$ d' \
| awk '{print $1"\t"$2}' \
> zr3616_5x-exonUTR-counts.txt

### 4e. Intron

In [48]:
%%bash
for f in *bed
do
    /opt/homebrew/bin/intersectBed \
    -u \
    -a ${f} \
    -b ../../genome-feature-files/cgigas_uk_roslin_v1_intron.bed \
    > ${f}-intron
done

In [49]:
#Check output
!head *intron

==> zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth.bed-intron <==
NC_047559.1	360322	360324
NC_047559.1	360361	360363
NC_047559.1	361347	361349
NC_047559.1	364329	364331
NC_047559.1	375341	375343
NC_047559.1	375360	375362
NC_047559.1	376111	376113
NC_047559.1	376170	376172
NC_047559.1	376962	376964
NC_047559.1	377335	377337

==> zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth.bed-intron <==
NC_047559.1	18234	18236
NC_047559.1	61081	61083
NC_047559.1	68070	68072
NC_047559.1	100249	100251
NC_047559.1	100276	100278
NC_047559.1	100305	100307
NC_047559.1	100319	100321
NC_047559.1	100440	100442
NC_047559.1	100454	100456
NC_047559.1	101107	101109

==> zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth.bed-intron <==
NC_047559.1	10270	10272
NC_047559.1	10292	10294
NC_047559.1	10314	10316
NC_047559.1	10358	10360
NC_047559.1	10380	10382
NC_047559.1	10391	10393
NC_047559.1	10402	10404
NC_047559.1	10413	10415
NC_047559.1	10


==> zr3616_union-averages_5x.bedgraph.NO-SNPs-Meth.bed-intron <==
NC_047559.1	61996	61998
NC_047559.1	110795	110797
NC_047559.1	356335	356337
NC_047559.1	356378	356380
NC_047559.1	356395	356397
NC_047559.1	356430	356432
NC_047559.1	356436	356438
NC_047559.1	356532	356534
NC_047559.1	356685	356687
NC_047559.1	356699	356701

==> zr3616_union-averages_5x.bedgraph.NO-SNPs-sparseMeth.bed-intron <==
NC_047559.1	60313	60315
NC_047559.1	60371	60373
NC_047559.1	60492	60494
NC_047559.1	61081	61083
NC_047559.1	62078	62080
NC_047559.1	63068	63070
NC_047559.1	63072	63074
NC_047559.1	63078	63080
NC_047559.1	64815	64817
NC_047559.1	66982	66984

==> zr3616_union-averages_5x.bedgraph.NO-SNPs-unMeth.bed-intron <==
NC_047559.1	10155	10157
NC_047559.1	10215	10217
NC_047559.1	10270	10272
NC_047559.1	10292	10294
NC_047559.1	10314	10316
NC_047559.1	10358	10360
NC_047559.1	10380	10382
NC_047559.1	10391	10393
NC_047559.1	10402	10404
NC_047559.1	10413	10415


In [50]:
#Count number of overlaps
!wc -l *intron

  441010 zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth.bed-intron
  361922 zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth.bed-intron
 2370103 zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth.bed-intron
  431889 zr3616_2_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth.bed-intron
  359018 zr3616_2_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth.bed-intron
 2400993 zr3616_2_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth.bed-intron
  442471 zr3616_3_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth.bed-intron
  346894 zr3616_3_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth.bed-intron
 2372125 zr3616_3_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth.bed-intron
  464828 zr3616_4_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth.bed-intron
  372558 zr3616_4_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph

In [51]:
#Get line counts for each fine
# Remove 28th line (total entries)
#Ensure output is tab-delimited
#Save output
!wc -l *-intron \
| sed '28,$ d' \
| awk '{print $1"\t"$2}' \
> zr3616_5x-intron-counts.txt

### 4f. Upstream flanks

In [52]:
%%bash
for f in *bed
do
    /opt/homebrew/bin/intersectBed \
    -u \
    -a ${f} \
    -b ../../genome-feature-files/cgigas_uk_roslin_v1_upstream.gff \
    > ${f}-upstreamFlanks
done

In [53]:
#Check output
!head *upstreamFlanks

==> zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth.bed-upstreamFlanks <==
NC_047559.1	576634	576636
NC_047559.1	576752	576754
NC_047559.1	1468258	1468260
NC_047559.1	1800917	1800919
NC_047559.1	1800924	1800926
NC_047559.1	2253122	2253124
NC_047559.1	3763635	3763637
NC_047559.1	3763649	3763651
NC_047559.1	3763653	3763655
NC_047559.1	3763678	3763680

==> zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth.bed-upstreamFlanks <==
NC_047559.1	9237	9239
NC_047559.1	9658	9660
NC_047559.1	9661	9663
NC_047559.1	335850	335852
NC_047559.1	335858	335860
NC_047559.1	335878	335880
NC_047559.1	335886	335888
NC_047559.1	335892	335894
NC_047559.1	576308	576310
NC_047559.1	576693	576695

==> zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth.bed-upstreamFlanks <==
NC_047559.1	9122	9124
NC_047559.1	9140	9142
NC_047559.1	9159	9161
NC_047559.1	9240	9242
NC_047559.1	9664	9666
NC_047559.1	9774	9776
NC_047559.1	9781	9783
NC_047559.1	9787	9


==> zr3616_union-averages_5x.bedgraph.NO-SNPs-sparseMeth.bed-upstreamFlanks <==
NC_047559.1	8979	8981
NC_047559.1	9658	9660
NC_047559.1	141708	141710
NC_047559.1	141717	141719
NC_047559.1	141777	141779
NC_047559.1	141800	141802
NC_047559.1	141853	141855
NC_047559.1	141858	141860
NC_047559.1	141868	141870
NC_047559.1	141885	141887

==> zr3616_union-averages_5x.bedgraph.NO-SNPs-unMeth.bed-upstreamFlanks <==
NC_047559.1	8970	8972
NC_047559.1	9122	9124
NC_047559.1	9140	9142
NC_047559.1	9159	9161
NC_047559.1	9237	9239
NC_047559.1	9240	9242
NC_047559.1	9603	9605
NC_047559.1	9661	9663
NC_047559.1	9664	9666
NC_047559.1	9774	9776


In [54]:
#Count number of overlaps
!wc -l *upstreamFlanks

    4883 zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth.bed-upstreamFlanks
   15102 zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth.bed-upstreamFlanks
  365079 zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth.bed-upstreamFlanks
    4865 zr3616_2_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth.bed-upstreamFlanks
   15819 zr3616_2_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth.bed-upstreamFlanks
  366613 zr3616_2_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth.bed-upstreamFlanks
    4934 zr3616_3_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth.bed-upstreamFlanks
   15049 zr3616_3_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth.bed-upstreamFlanks
  365126 zr3616_3_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth.bed-upstreamFlanks
    5239 zr3616_4_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth.bed-u

In [55]:
#Get line counts for each fine
# Remove 28th line (total entries)
#Ensure output is tab-delimited
#Save output
!wc -l *-upstreamFlanks \
| sed '28,$ d' \
| awk '{print $1"\t"$2}' \
> zr3616_5x-upstreamFlanks-counts.txt

### 4g. Downstream flanks

In [56]:
%%bash
for f in *bed
do
    /opt/homebrew/bin/intersectBed \
    -u \
    -a ${f} \
    -b ../../genome-feature-files/cgigas_uk_roslin_v1_downstream.gff \
    > ${f}-downstreamFlanks
done

In [57]:
#Check output
!head *downstreamFlanks

==> zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth.bed-downstreamFlanks <==
NC_047559.1	264885	264887
NC_047559.1	264911	264913
NC_047559.1	264924	264926
NC_047559.1	344440	344442
NC_047559.1	344447	344449
NC_047559.1	344477	344479
NC_047559.1	344549	344551
NC_047559.1	344794	344796
NC_047559.1	344812	344814
NC_047559.1	344829	344831

==> zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth.bed-downstreamFlanks <==
NC_047559.1	258442	258444
NC_047559.1	264959	264961
NC_047559.1	265013	265015
NC_047559.1	265028	265030
NC_047559.1	265111	265113
NC_047559.1	326295	326297
NC_047559.1	326317	326319
NC_047559.1	344861	344863
NC_047559.1	345009	345011
NC_047559.1	434413	434415

==> zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth.bed-downstreamFlanks <==
NC_047559.1	16061	16063
NC_047559.1	16105	16107
NC_047559.1	16112	16114
NC_047559.1	16220	16222
NC_047559.1	16260	16262
NC_047559.1	16289	16291
NC_047559.1	16310	16312
NC


==> zr3616_8_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth.bed-downstreamFlanks <==
NC_047559.1	16061	16063
NC_047559.1	16105	16107
NC_047559.1	16112	16114
NC_047559.1	16220	16222
NC_047559.1	16260	16262
NC_047559.1	16289	16291
NC_047559.1	16310	16312
NC_047559.1	16369	16371
NC_047559.1	16409	16411
NC_047559.1	16438	16440

==> zr3616_union-averages_5x.bedgraph.NO-SNPs-Meth.bed-downstreamFlanks <==
NC_047559.1	433588	433590
NC_047559.1	433598	433600
NC_047559.1	576634	576636
NC_047559.1	576693	576695
NC_047559.1	576752	576754
NC_047559.1	576866	576868
NC_047559.1	576880	576882
NC_047559.1	577126	577128
NC_047559.1	577456	577458
NC_047559.1	1010121	1010123

==> zr3616_union-averages_5x.bedgraph.NO-SNPs-sparseMeth.bed-downstreamFlanks <==
NC_047559.1	139183	139185
NC_047559.1	141853	141855
NC_047559.1	141858	141860
NC_047559.1	141868	141870
NC_047559.1	141885	141887
NC_047559.1	141888	141890
NC_047559.1	141894	141896
NC_047559.1	141905	141907
NC_047559.1	141912	141914
N

In [58]:
#Count number of overlaps
!wc -l *downstreamFlanks

   20108 zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth.bed-downstreamFlanks
   26394 zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth.bed-downstreamFlanks
  304826 zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth.bed-downstreamFlanks
   18944 zr3616_2_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth.bed-downstreamFlanks
   26915 zr3616_2_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth.bed-downstreamFlanks
  307855 zr3616_2_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth.bed-downstreamFlanks
   19824 zr3616_3_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth.bed-downstreamFlanks
   25556 zr3616_3_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth.bed-downstreamFlanks
  306478 zr3616_3_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth.bed-downstreamFlanks
   20462 zr3616_4_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.

In [59]:
#Get line counts for each fine
# Remove 28th line (total entries)
#Ensure output is tab-delimited
#Save output
!wc -l *-downstreamFlanks \
| sed '28,$ d' \
| awk '{print $1"\t"$2}' \
> zr3616_5x-downstreamFlanks-counts.txt

### 4h. Intergenic regions

In [60]:
%%bash
for f in *bed
do
    /opt/homebrew/bin/intersectBed \
    -u \
    -a ${f} \
    -b ../../genome-feature-files/cgigas_uk_roslin_v1_intergenic.bed \
    > ${f}-intergenic
done

In [61]:
#Check output
!head *intergenic

==> zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth.bed-intergenic <==
NC_047559.1	1547	1549
NC_047559.1	1571	1573
NC_047559.1	2267	2269
NC_047559.1	2291	2293
NC_047559.1	4073	4075
NC_047559.1	4791	4793
NC_047559.1	4835	4837
NC_047559.1	4843	4845
NC_047559.1	5605	5607
NC_047559.1	5613	5615

==> zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth.bed-intergenic <==
NC_047559.1	4887	4889
NC_047559.1	4909	4911
NC_047559.1	5500	5502
NC_047559.1	7716	7718
NC_047559.1	7814	7816
NC_047559.1	23610	23612
NC_047559.1	24932	24934
NC_047559.1	24934	24936
NC_047559.1	26463	26465
NC_047559.1	26485	26487

==> zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth.bed-intergenic <==
NC_047559.1	5883	5885
NC_047559.1	20252	20254
NC_047559.1	20297	20299
NC_047559.1	20319	20321
NC_047559.1	20341	20343
NC_047559.1	20363	20365
NC_047559.1	20385	20387
NC_047559.1	20407	20409
NC_047559.1	20429	20431
NC_047559.1	20451	20453

==> zr3616_2_R1_val


==> zr3616_union-averages_5x.bedgraph.NO-SNPs-unMeth.bed-intergenic <==
NC_047559.1	5883	5885
NC_047559.1	8295	8297
NC_047559.1	12439	12441
NC_047559.1	12503	12505
NC_047559.1	12520	12522
NC_047559.1	12906	12908
NC_047559.1	12923	12925
NC_047559.1	20252	20254
NC_047559.1	20297	20299
NC_047559.1	20319	20321


In [62]:
#Count number of overlaps
!wc -l *intergenic

   35770 zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth.bed-intergenic
  155853 zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth.bed-intergenic
 2389807 zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth.bed-intergenic
   37568 zr3616_2_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth.bed-intergenic
  159001 zr3616_2_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth.bed-intergenic
 2406131 zr3616_2_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth.bed-intergenic
   37512 zr3616_3_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth.bed-intergenic
  150346 zr3616_3_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth.bed-intergenic
 2372012 zr3616_3_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth.bed-intergenic
   39199 zr3616_4_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth.bed-intergenic
  163198 zr3616_4_R1_val_1

In [63]:
#Get line counts for each fine
# Remove 28th line (total entries)
#Ensure output is tab-delimited
#Save output
!wc -l *-intergenic \
| sed '28,$ d' \
| awk '{print $1"\t"$2}' \
> zr3616_5x-intergenic-counts.txt

### 4i. lncRNA

In [64]:
%%bash
for f in *bed
do
    /opt/homebrew/bin/intersectBed \
    -u \
    -a ${f} \
    -b ../../genome-feature-files/cgigas_uk_roslin_v1_lncRNA.gff \
    > ${f}-lncRNA
done

In [65]:
#Check output
!head *lncRNA

==> zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth.bed-lncRNA <==
NC_047559.1	1664457	1664459
NC_047559.1	1664745	1664747
NC_047559.1	1664773	1664775
NC_047559.1	1664902	1664904
NC_047559.1	1665259	1665261
NC_047559.1	1688362	1688364
NC_047559.1	1688423	1688425
NC_047559.1	1688433	1688435
NC_047559.1	1688466	1688468
NC_047559.1	2139066	2139068

==> zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth.bed-lncRNA <==
NC_047559.1	10899	10901
NC_047559.1	255751	255753
NC_047559.1	255789	255791
NC_047559.1	416920	416922
NC_047559.1	417337	417339
NC_047559.1	418447	418449
NC_047559.1	419514	419516
NC_047559.1	786896	786898
NC_047559.1	789201	789203
NC_047559.1	789687	789689

==> zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth.bed-lncRNA <==
NC_047559.1	10270	10272
NC_047559.1	10292	10294
NC_047559.1	10314	10316
NC_047559.1	10358	10360
NC_047559.1	10380	10382
NC_047559.1	10391	10393
NC_047559.1	10402	10404
NC_047559.1	10


==> zr3616_union-averages_5x.bedgraph.NO-SNPs-Meth.bed-lncRNA <==
NC_047559.1	417944	417946
NC_047559.1	418038	418040
NC_047559.1	418118	418120
NC_047559.1	418153	418155
NC_047559.1	418166	418168
NC_047559.1	418179	418181
NC_047559.1	418646	418648
NC_047559.1	418665	418667
NC_047559.1	419784	419786
NC_047559.1	419933	419935

==> zr3616_union-averages_5x.bedgraph.NO-SNPs-sparseMeth.bed-lncRNA <==
NC_047559.1	255751	255753
NC_047559.1	255789	255791
NC_047559.1	415945	415947
NC_047559.1	415975	415977
NC_047559.1	415998	416000
NC_047559.1	416071	416073
NC_047559.1	416078	416080
NC_047559.1	416088	416090
NC_047559.1	416920	416922
NC_047559.1	416993	416995

==> zr3616_union-averages_5x.bedgraph.NO-SNPs-unMeth.bed-lncRNA <==
NC_047559.1	10155	10157
NC_047559.1	10215	10217
NC_047559.1	10270	10272
NC_047559.1	10292	10294
NC_047559.1	10314	10316
NC_047559.1	10358	10360
NC_047559.1	10380	10382
NC_047559.1	10391	10393
NC_047559.1	10402	10404
NC_047559.1	10413	10415


In [66]:
#Count number of overlaps
!wc -l *lncRNA

   16324 zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth.bed-lncRNA
   24360 zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth.bed-lncRNA
  215175 zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth.bed-lncRNA
   15369 zr3616_2_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth.bed-lncRNA
   24724 zr3616_2_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth.bed-lncRNA
  218468 zr3616_2_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth.bed-lncRNA
   15533 zr3616_3_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth.bed-lncRNA
   23462 zr3616_3_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth.bed-lncRNA
  217209 zr3616_3_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth.bed-lncRNA
   16604 zr3616_4_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth.bed-lncRNA
   25814 zr3616_4_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph

In [67]:
#Get line counts for each fine
# Remove 28th line (total entries)
#Ensure output is tab-delimited
#Save output
!wc -l *-lncRNA \
| sed '28,$ d' \
| awk '{print $1"\t"$2}' \
> zr3616_5x-lncRNA-counts.txt

### 4j. Transposable elements

In [68]:
%%bash
for f in *bed
do
    /opt/homebrew/bin/intersectBed \
    -u \
    -a ${f} \
    -b ../../genome-feature-files/cgigas_uk_roslin_v1_rm.te.bed \
    > ${f}-TE
done

In [69]:
#Check output
!head *TE

==> zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth.bed-TE <==
NC_047559.1	91258	91260
NC_047559.1	91312	91314
NC_047559.1	232127	232129
NC_047559.1	234978	234980
NC_047559.1	264885	264887
NC_047559.1	264911	264913
NC_047559.1	264924	264926
NC_047559.1	293248	293250
NC_047559.1	294921	294923
NC_047559.1	294970	294972

==> zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth.bed-TE <==
NC_047559.1	26463	26465
NC_047559.1	26485	26487
NC_047559.1	26966	26968
NC_047559.1	27211	27213
NC_047559.1	44183	44185
NC_047559.1	46646	46648
NC_047559.1	47794	47796
NC_047559.1	50864	50866
NC_047559.1	50869	50871
NC_047559.1	50878	50880

==> zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth.bed-TE <==
NC_047559.1	15746	15748
NC_047559.1	24588	24590
NC_047559.1	26419	26421
NC_047559.1	26448	26450
NC_047559.1	26509	26511
NC_047559.1	26532	26534
NC_047559.1	26547	26549
NC_047559.1	26555	26557
NC_047559.1	26561	26563
NC_047559.1	26573	26


==> zr3616_union-averages_5x.bedgraph.NO-SNPs-sparseMeth.bed-TE <==
NC_047559.1	45010	45012
NC_047559.1	46646	46648
NC_047559.1	47276	47278
NC_047559.1	47794	47796
NC_047559.1	50821	50823
NC_047559.1	50848	50850
NC_047559.1	50857	50859
NC_047559.1	50864	50866
NC_047559.1	50869	50871
NC_047559.1	50878	50880

==> zr3616_union-averages_5x.bedgraph.NO-SNPs-unMeth.bed-TE <==
NC_047559.1	15746	15748
NC_047559.1	24588	24590
NC_047559.1	25485	25487
NC_047559.1	25667	25669
NC_047559.1	26135	26137
NC_047559.1	26419	26421
NC_047559.1	26448	26450
NC_047559.1	26463	26465
NC_047559.1	26485	26487
NC_047559.1	26509	26511


In [70]:
#Count number of overlaps
!wc -l *TE

  246906 zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth.bed-TE
  345635 zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth.bed-TE
 2341295 zr3616_1_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth.bed-TE
  248977 zr3616_2_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth.bed-TE
  352367 zr3616_2_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth.bed-TE
 2353758 zr3616_2_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth.bed-TE
  244808 zr3616_3_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth.bed-TE
  334790 zr3616_3_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth.bed-TE
 2329821 zr3616_3_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-unMeth.bed-TE
  252579 zr3616_4_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-Meth.bed-TE
  365887 zr3616_4_R1_val_1_val_1_val_1_bismark_bt2_pe._5x.bedgraph.NO-SNPs-sparseMeth.bed-TE
 2452141 zr36

In [71]:
#Get line counts for each fine
# Remove 28th line (total entries)
#Ensure output is tab-delimited
#Save output
!wc -l *-TE \
| sed '28,$ d' \
| awk '{print $1"\t"$2}' \
> zr3616_5x-TE-counts.txt